In [1]:
import tensorflow_decision_forests as tfdf

import tensorflow as tf

import os
import numpy as np
import pandas as pd
import tensorflow as tf
import math

import dtreeviz

from matplotlib import pyplot as plt
from IPython import display

2023-04-27 08:10:08.921419: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-04-27 08:10:09.084389: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-04-27 08:10:09.085660: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-04-27 08:10:10.174711: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [2]:
# avoid "Arial font not found warnings"
import logging
logging.getLogger('matplotlib.font_manager').setLevel(level=logging.CRITICAL)

display.set_matplotlib_formats('retina') # generate hires plots

np.random.seed(1234)  # reproducible plots/data for explanatory reasons

/tmp/ipykernel_101/745931794.py:5: DeprecationWarning: `set_matplotlib_formats` is deprecated since IPython 7.23, directly use `matplotlib_inline.backend_inline.set_matplotlib_formats()`


In [3]:
# Split the dataset into a training and a testing dataset.

def split_dataset(dataset, test_ratio=0.30):
  """Splits a panda dataframe in two."""
  test_indices = np.random.rand(len(dataset)) < test_ratio
  return dataset[~test_indices], dataset[test_indices]



In [4]:
df = pd.read_csv('covid-19_symptoms_dataset.csv', sep=",")

In [5]:
train_ds_pd, test_ds_pd = split_dataset(df)
print("{} examples in training, {} examples for testing.".format(
    len(train_ds_pd), len(test_ds_pd)))

1785 examples in training, 790 examples for testing.


In [6]:
df

fever  bodyPain  age  runnyNose  diffBreath  infectionProb
0       102         0    9          0          -1              0
1       102         0   10          0           0              1
2       104         0   33          1          -1              0
3       101         1   59          0           1              0
4        99         0   98          0           0              0
...     ...       ...  ...        ...         ...            ...
2570     99         0   90          0           0              1
2571    100         0   53          0          -1              1
2572    101         0   44          1           0              0
2573    102         0   97          0          -1              1
2574    104         1   62          1          -1              1

[2575 rows x 6 columns]

In [7]:
target = 'infectionProb'

classes = list(df[target].unique())

df[target] = df[target].map(classes.index)

In [8]:
# Split into training and test sets
train_ds_pd, test_ds_pd = split_dataset(df)
print(f"{len(train_ds_pd)} examples in training, {len(test_ds_pd)} examples for testing.")

# Convert to tensorflow data sets
train_ds = tfdf.keras.pd_dataframe_to_tf_dataset(train_ds_pd, label=target)
test_ds = tfdf.keras.pd_dataframe_to_tf_dataset(test_ds_pd, label=target)

1800 examples in training, 775 examples for testing.


In [9]:
# Specify the model.
model_1 = tfdf.keras.RandomForestModel(verbose=2)

# Train the model.
model_1.fit(train_ds)

Use 16 thread(s) for training
Use /tmp/tmpwrasv099 as temporary training directory
Reading training dataset...


2023-04-27 08:10:13.695402: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_2' with dtype int64 and shape [1800]
	 [[{{node Placeholder/_2}}]]


Training tensor examples:
Features: {'fever': <tf.Tensor 'data:0' shape=(None,) dtype=int64>, 'bodyPain': <tf.Tensor 'data_1:0' shape=(None,) dtype=int64>, 'age': <tf.Tensor 'data_2:0' shape=(None,) dtype=int64>, 'runnyNose': <tf.Tensor 'data_3:0' shape=(None,) dtype=int64>, 'diffBreath': <tf.Tensor 'data_4:0' shape=(None,) dtype=int64>}
Label: Tensor("data_5:0", shape=(None,), dtype=int64)
Weights: None
Normalized tensor features:
 {'fever': SemanticTensor(semantic=<Semantic.NUMERICAL: 1>, tensor=<tf.Tensor 'Cast:0' shape=(None,) dtype=float32>), 'bodyPain': SemanticTensor(semantic=<Semantic.NUMERICAL: 1>, tensor=<tf.Tensor 'Cast_1:0' shape=(None,) dtype=float32>), 'age': SemanticTensor(semantic=<Semantic.NUMERICAL: 1>, tensor=<tf.Tensor 'Cast_2:0' shape=(None,) dtype=float32>), 'runnyNose': SemanticTensor(semantic=<Semantic.NUMERICAL: 1>, tensor=<tf.Tensor 'Cast_3:0' shape=(None,) dtype=float32>), 'diffBreath': SemanticTensor(semantic=<Semantic.NUMERICAL: 1>, tensor=<tf.Tensor 'Cast_

[INFO 23-04-27 08:10:16.5264 CEST kernel.cc:773] Start Yggdrasil model training
[INFO 23-04-27 08:10:16.5264 CEST kernel.cc:774] Collect training examples
[INFO 23-04-27 08:10:16.5265 CEST kernel.cc:787] Dataspec guide:
column_guides {
  column_name_pattern: "^__LABEL$"
  type: CATEGORICAL
  categorial {
    min_vocab_frequency: 0
    max_vocab_count: -1
  }
}
default_column_guide {
  categorial {
    max_vocab_count: 2000
  }
  discretized_numerical {
    maximum_num_bins: 255
  }
}
ignore_columns_without_guides: false
detect_numerical_as_discretized_numerical: false

[INFO 23-04-27 08:10:16.5276 CEST kernel.cc:393] Number of batches: 2
[INFO 23-04-27 08:10:16.5276 CEST kernel.cc:394] Number of examples: 1800
[INFO 23-04-27 08:10:16.5277 CEST kernel.cc:794] Training dataset:
Number of records: 1800
Number of columns: 6

Number of columns by type:
	NUMERICAL: 5 (83.3333%)
	CATEGORICAL: 1 (16.6667%)

Columns:

NUMERICAL: 5 (83.3333%)
	1: "age" NUMERICAL mean:50.5817 min:1 max:100 sd:28.

[INFO 23-04-27 08:10:17.0525 CEST kernel.cc:1242] Loading model from path /tmp/tmpwrasv099/model/ with prefix c2dddae1189143aa
[INFO 23-04-27 08:10:17.1997 CEST decision_forest.cc:660] Model loaded with 300 root(s), 144982 node(s), and 5 input feature(s).
[INFO 23-04-27 08:10:17.1997 CEST abstract_model.cc:1311] Engine "RandomForestOptPred" built
[INFO 23-04-27 08:10:17.1997 CEST kernel.cc:1074] Use fast generic engine


Model trained in 0:00:00.982420
Compiling model...


2023-04-27 08:10:17.261267: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_3' with dtype int64 and shape [1800]
	 [[{{node Placeholder/_3}}]]


Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: could not get source code
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert


Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: could not get source code
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert


Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: could not get source code
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Model compiled.


In [10]:
model_1.compile(metrics=["accuracy"])
evaluation = model_1.evaluate(test_ds, return_dict=True)
print()

for name, value in evaluation.items():
  print(f"{name}: {value:.4f}")

2023-04-27 08:10:18.295700: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_0' with dtype int64 and shape [775]
	 [[{{node Placeholder/_0}}]]


1/1 [==============================] - 0s 224ms/step - loss: 0.0000e+00 - accuracy: 0.5187

loss: 0.0000
accuracy: 0.5187


In [11]:
model_1.save("/tmp/my_saved_model")

INFO:tensorflow:Assets written to: /tmp/my_saved_model/assets


INFO:tensorflow:Assets written to: /tmp/my_saved_model/assets


In [12]:
model_1.summary()

Model: "random_forest_model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
Total params: 1
Trainable params: 0
Non-trainable params: 1
_________________________________________________________________
Type: "RANDOM_FOREST"
Task: CLASSIFICATION
Label: "__LABEL"

Input Features (5):
	age
	bodyPain
	diffBreath
	fever
	runnyNose

No weights

Variable Importance: INV_MEAN_MIN_DEPTH:
    1.        "age"  0.527587 ################
    2. "diffBreath"  0.234063 ####
    3.      "fever"  0.208827 ###
    4.  "runnyNose"  0.142771 
    5.   "bodyPain"  0.131770 

Variable Importance: NUM_AS_ROOT:
    1.        "age" 131.000000 ################
    2. "diffBreath" 99.000000 ###########
    3.  "runnyNose" 45.000000 #####
    4.      "fever" 21.000000 ##
    5.   "bodyPain"  4.000000 

Variable Importance: NUM_NODES:
    1.        "age" 38835.000000 ################
    2.      "fever" 16983.000000 #####
    3. "

In [13]:
# The input features
model_1.make_inspector().features()

["age" (1; #1),
 "bodyPain" (1; #2),
 "diffBreath" (1; #3),
 "fever" (1; #4),
 "runnyNose" (1; #5)]

In [14]:
# The feature importances
model_1.make_inspector().variable_importances()

{'NUM_NODES': [("age" (1; #1), 38835.0),
  ("fever" (1; #4), 16983.0),
  ("diffBreath" (1; #3), 6848.0),
  ("bodyPain" (1; #2), 5035.0),
  ("runnyNose" (1; #5), 4640.0)],
 'INV_MEAN_MIN_DEPTH': [("age" (1; #1), 0.5275870166747533),
  ("diffBreath" (1; #3), 0.23406343558257775),
  ("fever" (1; #4), 0.20882725939751562),
  ("runnyNose" (1; #5), 0.14277098729374485),
  ("bodyPain" (1; #2), 0.13176977089860856)],
 'NUM_AS_ROOT': [("age" (1; #1), 131.0),
  ("diffBreath" (1; #3), 99.0),
  ("runnyNose" (1; #5), 45.0),
  ("fever" (1; #4), 21.0),
  ("bodyPain" (1; #2), 4.0)],
 'SUM_SCORE': [("age" (1; #1), 97444.44377884663),
  ("fever" (1; #4), 40451.805595961996),
  ("diffBreath" (1; #3), 16389.602919984085),
  ("bodyPain" (1; #2), 11407.169145895983),
  ("runnyNose" (1; #5), 10409.045589556132)]}

In [15]:
# Tell dtreeviz about training data and model
features = [f.name for f in model_1.make_inspector().features()]
viz_cmodel = dtreeviz.model(model_1,
                           tree_index=3,
                           X_train=train_ds_pd[features],
                           y_train=train_ds_pd[target],
                           feature_names=features,
                           target_name=target,
                           class_names=classes)

In [16]:
viz_cmodel.view(scale=1.2)

In [17]:
print(features)

['age', 'bodyPain', 'diffBreath', 'fever', 'runnyNose']


In [18]:
model_1.save("my_model")

INFO:tensorflow:Assets written to: my_model/assets


INFO:tensorflow:Assets written to: my_model/assets


In [19]:
df.head(1)

fever  bodyPain  age  runnyNose  diffBreath  infectionProb
0    102         0    9          0          -1              0

df[~'infectionProb']

In [20]:
test = tfdf.keras.pd_dataframe_to_tf_dataset(df.loc[:, df.columns!='infectionProb'].head(99))
t1 = df['infectionProb'].head(99)

In [21]:
tes = model_1.predict(test, verbose=0)

2023-04-27 08:10:54.360760: I tensorflow/core/common_runtime/executor.cc:1197] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'Placeholder/_3' with dtype int64 and shape [99]
	 [[{{node Placeholder/_3}}]]


In [22]:
k = []
i = 0
cnt = 0
for t in tes:
    if(t[0]>=0.5):
        k.append(1)
        print("1 - " + str(t1[i]))
        if(t1[i] == 1):
            cnt += 1
    else:
        k.append(0)
        print("0 - " + str(t1[i]))
        if(t1[i] == 0):
            cnt += 1
    i+=1
print(cnt/len(t1))

1 - 0
1 - 1
1 - 0
0 - 0
0 - 0
1 - 1
0 - 0
1 - 1
0 - 1
1 - 1
1 - 1
0 - 0
0 - 0
0 - 0
1 - 0
1 - 1
1 - 1
0 - 0
1 - 1
0 - 0
0 - 0
1 - 0
0 - 1
1 - 1
0 - 0
0 - 0
0 - 1
1 - 1
0 - 1
0 - 0
1 - 1
0 - 0
1 - 1
1 - 1
1 - 1
0 - 1
0 - 1
0 - 0
0 - 0
0 - 0
1 - 1
0 - 0
0 - 1
0 - 0
1 - 0
0 - 0
1 - 1
1 - 1
0 - 1
1 - 1
0 - 0
0 - 0
0 - 0
1 - 1
1 - 1
1 - 1
0 - 0
0 - 0
0 - 0
1 - 1
0 - 0
0 - 0
1 - 1
1 - 1
1 - 0
0 - 0
1 - 1
0 - 0
1 - 0
1 - 0
1 - 1
1 - 1
1 - 1
0 - 1
0 - 0
1 - 0
1 - 0
1 - 0
1 - 1
0 - 0
0 - 0
0 - 0
1 - 1
0 - 0
0 - 1
1 - 0
0 - 0
0 - 0
1 - 1
0 - 0
0 - 0
1 - 1
1 - 1
0 - 0
1 - 1
1 - 1
0 - 1
0 - 0
0 - 0
0.7676767676767676
